# Prep

In [11]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [12]:
def addToDB(DB_NAME,COL_NAME,PATH,FILE):
    '''
    Imports a file into mongoDB
    
    Parameters:
    --------
    DB_NAME : Name of the database to connect to
    COL_NAME: Name of the collection to create
    PATH    : Path to folder with the file
    FILE  : Filename
    
    Returns:
    --------
    Collection COL_NAME in DB_NAME database
    '''
    !mongoimport --db {DB_NAME} --collection {COL_NAME} --file {PATH+FILE} --batchSize 1
    print(f'Collection {COL_NAME} in {DB_NAME} database created')

In [68]:
from bson.objectid import ObjectId

def show_doc(db, collection, id):
    '''
    Finds a document by 'id' and prints contents to the console
    
    Parameters:
    --------
    db         : database name
    collection : mongodb collection
    id         : mongodb document id
    
    Returns:
    --------
    Prints first 100 symbols of each document's key to console
    '''
    
    doc = db[collection].find_one({'_id':ObjectId(id)})
    for k in doc:
        print(f"{k} : {str(doc[k])}")

# Some comands to keep dbs clean

In [ ]:
# deletes all 'meta' fields from all docs
# htmlCol.update({}, {$unset: {meta:1}}, false, true); # mongo shell comand
htmlCol.update({}, {'$unset': {'meta':1}}, multi=True) # pymongo way

In [ ]:
# leaves only unique documents by 'url' field

htmlCol.create_index(
    "url",
    unique=True
)

In [ ]:
# pymongo 'find' returns cursor that allows iterating through results
# calling first object [0] allows accessing the dictionary with results
# the ['html'] is the key in the dictionary
html = htmlCol.find({'url':'http://www.msnbc.com/velshi-ruhle/watch/jeff-sessions-is-justifying-harsh-immigration-policy-with-the-bible-1256689731629'},\
            projection={'html':True, '_id':False})[0]['html']

In [ ]:
# find documents NOT containing a 'tag': regex expression
import re
tag = re.compile('dek___3AQpw.')
docs = htmlCol.find({"html" : {'$not': tag}})
for d in docs[:20]: print(d['url'])

# Multithreading

In [ ]:
from multiprocessing import Process

# use multiprocessing to extract features
def func():
    DB_NAME = 'scrape'
    db = pm.MongoClient(host='localhost', port=27017, maxPoolSize=500)[DB_NAME]

    for collection in ['left','right']: docs_parser(db[collection])

proc = Process(target=func)
proc.start()

# Helpers

In [5]:
# For debugging turn on logging to console
import logging
logging.basicConfig(level=logging.DEBUG)
log = logging.getLogger(__name__)

# dependencies
import pymongo as pm

from resources.newspaper import newspaper
from resources.newspaper.newspaper.source import Source
from resources.newspaper.newspaper.article import Article

import bs4 as bs
from urllib.parse import urljoin
from dateutil.parser import parse as date_parser
from time import sleep
import random
import pytz

import requests

# Initialize PyMongo to work with MongoDBs
conn = 'mongodb://localhost:27017'
client = pm.MongoClient(conn, maxPoolSize=200)

# define db 
# DB_NAME = 'scrape'
DB_NAME = 'FINALP'
db = client[DB_NAME]

In [13]:
# powered by NewsAPI.org
SOURCES = {
    'left'  : [
        'https://newrepublic.com',
        'https://www.motherjones.com'
# 3. Slate
# 4. The Intercept
# 5. Daily Beast
# 6. The Atlantic
# 7. Washington Post
# 8. Politico
# 9. The Guardian
# 10. BBC
    ],
    'right' : [
        'https://www.breitbart.com'
# 2. Fox News
# 3. New York Post
# 4. The American Conservative
# 5. Washington Times
# 6. Daily Wire
# 7. The Fiscal Times
# 8. The Hill
# 9. The Daily Caller
# 10. Reason
    ]
}

In [2]:
def saveToDB(db, collection, url, html, meta={}):
    """
    Saves a document to mongoDB, making sure there are no duplicates by 
    'url' value
    
    Parameters:
    --------
    db, collection  : mongo db connection
    url, html, meta : values to store
    
    Returns:
    --------
    Saved document
    """
    collection = db[collection]
    collection.update_one(
        {'url' : url},
        {
            '$set':
                {'url' : url,
                 'html' : html,
                 'meta' : meta
                }
        }
        ,
        upsert=True
    )
    log.debug(f'Saved to DB')

In [74]:
import datetime
def scrape(url, db, collection):
    '''
    Scrapes an article from the 'url' up to the 'latest_date'
    
    Parameters:
    --------
    url         : main news website url
    date        : YYYY-MM-DD
    db          : database name
    collection  : mongodb collection
    
    Returns:
    --------
    Article's html and features stored to db, 
    Article's publish date
    
    '''
    try:
        article = Article(url)
        article.download()
        # the below method may only extract a snippet... 
        # check the database for results of text extraction
        # and apply additional processing if needed after 
        # article has been stored in the DB
        # see code below Newrepublic for example
        article.parse()
    except Exception as e:
        log.critical(f'Data not saved: {e}')
        return datetime.datetime.now()
    
    saveToDB(db, collection, article.url, article.html, meta={
        'date'    :article.publish_date,
        'title'   :article.title,
        'text'    :article.text,
        'authors' :article.authors
    })
    
    return article.publish_date

# Newrepublic

In [78]:
# name of collection for this media
collection = 'newRep'
source = 'https://newrepublic.com/latest'
page   = 91

earliest_date = date_parser('2017-01-01')

while True:
    log.debug(f'PROCESSING PAGE: {page}')
    s = Source(source+'?page='+str(page))
    s.download()

    soup = bs.BeautifulSoup(s.html,'lxml')

    # line below needs to be updated per news source
    # to include the specific tags for article text 
    # defined differently for each site
    for section in soup.findAll('article'):
        url = urljoin(s.url, section.a['href'])
        log.debug(f'Processing url: {url}')
        
        article_date = scrape(url, db, collection)

    if article_date < earliest_date:
        log.debug(f'Reached earliest date requested: {article_date}')
        break
    page += 1

DEBUG:__main__:PROCESSING PAGE: 91
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /latest?page=91 HTTP/1.1" 200 74967
DEBUG:__main__:Processing url: https://newrepublic.com/article/146040/david-hockney-makes-splash
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/146040/david-hockney-makes-splash HTTP/1.1" 200 19287
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/146049/a-professor-kind-like-priest
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/146049/a-professor-kind-like-priest HTTP/1.1" 200 35450
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/146046/james-francos-brilliantly-bad-starring-role

DEBUG:__main__:Processing url: https://newrepublic.com/article/145964/broken-justice-system-led-sexual-harassment-crisis
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145964/broken-justice-system-led-sexual-harassment-crisis HTTP/1.1" 200 20417
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145961/trouble-golden-age-tv
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145961/trouble-golden-age-tv HTTP/1.1" 200 22202
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145952/toxic-chemical-industry-really-great-year
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145952/toxic-chemical-industr

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145421/anti-sanctuary-armies-local-officials-working-trump-administration-clampdown-undocumented-immigrants HTTP/1.1" 200 20674
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145810/century-women-fighting-back
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145810/century-women-fighting-back HTTP/1.1" 200 22812
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145813/cause-consequences-retail-apocalypse
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145813/cause-consequences-retail-apocalypse HTTP/1.1" 200 20403
DEBUG:__main__:Saved to DB
DE

DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145739/left-great-election-night-will-democrats-take-advantage HTTP/1.1" 200 19841
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145727/socialist-beat-one-virginias-powerful-republicans
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145727/socialist-beat-one-virginias-powerful-republicans HTTP/1.1" 200 21637
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145726/trumpism-without-trump-doesnt-work
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145726/trumpism-without-trump-doesnt-work HTTP/1.1" 200 19824
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145728/trumps-blank-check-sa

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145437/hidden-powers-margaret-atwood-alias-grace-makes-subversive-television HTTP/1.1" 200 22561
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145425/new-coal-crisis-loosening-environmental-regulations-trump-risks-making-health-hazard-critical
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/145425/new-coal-crisis-loosening-environmental-regulations-trump-risks-making-health-hazard-critical HTTP/1.1" 200 21831
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/145631/scott-pruitts-plot-sabotage-science-epa
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GE

...

DEBUG:__main__:Processing url: https://newrepublic.com/article/140070/case-unity
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/140070/case-unity HTTP/1.1" 200 22279
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/140065/myth-well-behaved-womens-march
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/140065/myth-well-behaved-womens-march HTTP/1.1" 200 20424
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/140063/problem-pussy
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/140063/problem-pussy HTTP/1.1" 200 18417
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139264/white-vans-and-black-suburbans HTTP/1.1" 200 21732
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139959/35-year-old-mayor-indiana-wowing-national-democrats
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139959/35-year-old-mayor-indiana-wowing-national-democrats HTTP/1.1" 200 19120
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139884/lefts-divisions-will-display-inauguration
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139884/lefts-divisions-will-display-inauguration HTTP/1.1" 200 18786
DEBUG:__main__:Saved to DB
DEBUG:__main__

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139843/primary-concerns-episode-40-donald-trumps-impunity-presidency
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139843/primary-concerns-episode-40-donald-trumps-impunity-presidency HTTP/1.1" 200 16462
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139817/donald-trump-wants-ignore-russia-worry-china
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139817/donald-trump-wants-ignore-russia-worry-china HTTP/1.1" 200 20798
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139761/can-kamala-harris-live-hype
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.conne

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139698/lurid-return-menendez-brothers HTTP/1.1" 200 18006
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139685/eric-holder-rescue
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139685/eric-holder-rescue HTTP/1.1" 200 19247
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://newrepublic.com/article/139679/walking-dully-along-dispatch-istanbul
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139679/walking-dully-along-dispatch-istanbul HTTP/1.1" 200 18715
DEBUG:__main__:Saved to DB
DEBUG:__main__:PROCESSING PAGE: 223
DEBUG:urllib3.connectionpool:Starting new HTTPS conn

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newrepublic.com:443
DEBUG:urllib3.connectionpool:https://newrepublic.com:443 "GET /article/139550/legacy-altamont HTTP/1.1" 200 23285
DEBUG:__main__:Saved to DB
DEBUG:__main__:Reached earliest date requested: 2016-12-29 00:00:00


In [79]:
# update text field to include more data
for doc in db[collection].find():
    soup = bs.BeautifulSoup(doc['html'],'lxml')
    text = ''
    for div in soup.findAll('div',{"class": "content-body"}):
        text += div.text
    if len(doc['meta']['text']) < len(text):
        db[collection].update_one(
            {'url' : doc['url']},
            {
                '$set':
                    {
                     'meta.text' : text
                    }
            }
            ,
            upsert=True
        )

In [80]:
url = 'https://newrepublic.com/article/139550/legacy-altamont'
doc = db[collection].find_one({'url':url})
doc['meta']['text']

'Altamont has by now acquired the kind of dynastic weight\nthat even the Rolling Stones, for all their grandiose posturing as they\npromoted the concert, could never have imagined. Today, when we talk about the\nend of the Sixties, we talk about Watergate and we talk about the Manson Family\nand we talk about Altamont. But no matter what moment we settle on, we agree\nthat the Sixties had an end: a moment\nwhen blind idealism was finally bested by unavoidable proof of man’s intrinsic\nviolence and egomania and greed. This view is a grim one, but it is also a\ncomfort. It means that any attempt to mitigate this Hobbesian brutality is not\njust a fool’s errand, but a dangerous one.\nBest to stay home.ALTAMONT: THE ROLLING STONES, THE HELLS ANGELS, AND THE INSIDE STORY OF ROCK’S DARKEST DAY by Joel SelvinDey Street Books, 368 pp., $27.99The story goes that the dream of Sixties ended because\nsomething weakened, something broke. Because the loving energy that emerged as\na dominant force i

# The Atlantic

In [82]:
utc=pytz.UTC

# name of collection for this media
collection = 'theAtlantic'
source = 'https://www.theatlantic.com/latest/'

# start 'page' at '1' but if you run across an error
# efficient way is to update this page to the same number
# where you experienced the error AFTER you correct the error in the code
# then rerun this cell
page   = 175

earliest_date = utc.localize(date_parser('2017-01-01'))

while True:
    log.debug(f'\n\n PROCESSING PAGE: {source+"?page="+str(page)}\n\n\
              ====================================\n\n')
    s = Source(source+'?page='+str(page))
    page += 1
    s.download()
    soup = bs.BeautifulSoup(s.html,'lxml')

    # line below needs to be updated per news source
    # to include the specific tags for article text 
    # defined differently for each site
    for section in soup.findAll('li', {"class":"article"}):
        url = urljoin(s.url, section.a['href'])
        log.debug(f'Processing url: {url}')
        
        try:
            article_date = scrape(url, db, collection)
        except Exception:
            article_date = earliest_date + 1 #to make sure scraping continues
        
        # the Atlantic blocks right away after few quick downloads
        # so it requires sleeping, testing showed 1 to 5 seconds is enough
#         sleep(random.uniform(1,5))

    try:
        if article_date < earliest_date:
            log.debug(f'Reached earliest date requested: {article_date}')
            break
    except Exception as e:
        log.debug(f'Exception: {e}')
        continue
    

DEBUG:__main__:

 PROCESSING PAGE: https://www.theatlantic.com/latest/?page=175



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /latest/?page=175 HTTP/1.1" 200 24434
DEBUG:__main__:Processing url: https://www.theatlantic.com/video/index/544403/jimmy-chin-interview-climbing-photography-film/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /video/index/544403/jimmy-chin-interview-climbing-photography-film/ HTTP/1.1" 200 30325
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2017/10/sexual-assault-plot-device-twist-liar-una/544340/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /entertainment/archive/2017/10/sexual

DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /international/archive/2017/10/beghazi-suspect-captured/544436/ HTTP/1.1" 200 30365
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/politics/archive/2017/10/how-did-these-guys-get-hired/544358/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /politics/archive/2017/10/how-did-these-guys-get-hired/544358/ HTTP/1.1" 200 33935
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/business/archive/2017/10/trump-fed-chair/544406/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /business/archive/2017/10/trump-fed-chair/544406/ HTTP/1.1" 200 34926
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/politics/archive/201

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /science/archive/2017/10/hubble-constant-neutron-stars/544080/ HTTP/1.1" 200 35814
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/technology/archive/2017/10/decorative-gourd-season/544232/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /technology/archive/2017/10/decorative-gourd-season/544232/ HTTP/1.1" 200 35415
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/politics/archive/2017/10/report-former-trump-chair-paul-manafort-and-partner-told-to-surrender/544331/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /politics/archive/2017/10/report-former-t

DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /international/archive/2017/10/catalonias-gamble/544259/ HTTP/1.1" 200 33171
DEBUG:__main__:Saved to DB
DEBUG:__main__:

 PROCESSING PAGE: https://www.theatlantic.com/latest/?page=177



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /latest/?page=177 HTTP/1.1" 200 24444
DEBUG:__main__:Processing url: https://www.theatlantic.com/newsletters/archive/2017/10/the-atlantic-daily-october-27-2017/544214/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /newsletters/archive/2017/10/the-atlantic-daily-october-27-2017/544214/ HTTP/1.1" 200 34066
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2017/10/the-atlantics-week-in-culture/544277/
DEBUG:urllib3.connectionp

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /health/archive/2017/10/will-microwave-popcorn-ruin-my-lungs/544173/ HTTP/1.1" 200 31250
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2017/10/the-killing-of-a-sacred-deer-review/544089/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /entertainment/archive/2017/10/the-killing-of-a-sacred-deer-review/544089/ HTTP/1.1" 200 32085
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/business/archive/2017/10/cookbooks-status-600-years/544164/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /business/archive/2017/10/cookbooks-status-600-y

...

DEBUG:__main__:Processing url: https://www.theatlantic.com/education/archive/2017/01/how-university-costs-keep-rising-despite-tuition-freezes/512036/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /education/archive/2017/01/how-university-costs-keep-rising-despite-tuition-freezes/512036/ HTTP/1.1" 200 36592
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/technology/archive/2017/01/the-best-twitter-account-i-followed-this-year/511868/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /technology/archive/2017/01/the-best-twitter-account-i-followed-this-year/511868/ HTTP/1.1" 200 32785
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/science/archive/2017/01/why-trump-will-be-influenced-by-his-conflicts-of-in

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2016/12/the-new-reality-tv/511907/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /entertainment/archive/2016/12/the-new-reality-tv/511907/ HTTP/1.1" 200 33768
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/education/archive/2016/12/5-numbers-that-explain-education-in-2016/511565/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /education/archive/2016/12/5-numbers-that-explain-education-in-2016/511565/ HTTP/1.1" 200 31651
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/liveblogs/2016/12/news-today/511892/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEB

DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /science/archive/2016/12/cdc-quarantine-rule-violate-civil-liberties/511823/ HTTP/1.1" 200 35488
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2016/12/alabama-game/511745/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /entertainment/archive/2016/12/alabama-game/511745/ HTTP/1.1" 200 32558
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/business/archive/2016/12/embracing-an-ordinary-economy/511208/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /business/archive/2016/12/embracing-an-ordinary-economy/511208/ HTTP/1.1" 200 34608
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/b

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/health/archive/2016/12/testicular-hysteria/511793/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /health/archive/2016/12/testicular-hysteria/511793/ HTTP/1.1" 200 36944
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/liveblogs/2016/12/news-today/511754/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /liveblogs/2016/12/news-today/511754/ HTTP/1.1" 200 39979
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/newsletters/archive/2016/12/the-atlantic-daily-parting-words/510275/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:44

DEBUG:__main__:Processing url: https://www.theatlantic.com/politics/archive/2016/12/the-atlantic-politics-policy-daily/511739/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /politics/archive/2016/12/the-atlantic-politics-policy-daily/511739/ HTTP/1.1" 200 32543
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/entertainment/archive/2016/12/remembering-carrie-fisher/511730/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connectionpool:https://www.theatlantic.com:443 "GET /entertainment/archive/2016/12/remembering-carrie-fisher/511730/ HTTP/1.1" 200 32672
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://www.theatlantic.com/photo/2016/12/christmas-down-under/511715/
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.theatlantic.com:443
DEBUG:urllib3.connection

# Politico

In [11]:
# setup
# use your newsapi key
# update collection, date and source
collection = 'Politoco'
page = 1
earliest_date = '2017-01-01'
latest_date = '2017-09-13'
source = 'politico'
pageSize = 100
apiKey = 'fd1386b678fd4524b2aa84e3bee1f8f7'

params = {
    'apiKey' : apiKey,
    'pageSize' : pageSize,
    'page' : page,
    'from' : earliest_date,
    'to'   : latest_date,
    'sources': source
}

# base url
api_url = 'https://newsapi.org/v2/everything?'

# get first request to obtain total news count
r = requests.get(api_url, params=params)
totalPages = r.json()['totalResults']//100
log.debug(f'Total pages ({pageSize} per page) for {source} results from {earliest_date} to {latest_date} is {totalPages}')

# scrape news
for p in range(page,totalPages+1):
    log.debug(f'\n\n PROCESSING PAGE: {source+"?page="+str(page)}\n\n\
              ====================================\n\n')
    
    params = {
        'apiKey' : apiKey,
        'pageSize' : pageSize,
        'page' : page,
        'from' : earliest_date,
        'to'   : latest_date,
        'sources': source
    }
    
    r = requests.get(api_url, params=params)

    page += 1
    
    if r.json()['articles']:
        for a in r.json()['articles']:
            try:
                log.debug(f"Processing url: {a['url']}")
                article_date = scrape(a['url'], db, collection)
            except Exception:
                article_date = earliest_date + 1
    else:
        log.debug(f"Response doesn't have articles. Response: {r.json()}")
        

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newsapi.org
DEBUG:urllib3.connectionpool:https://newsapi.org:443 "GET /v2/everything?apiKey=fd1386b678fd4524b2aa84e3bee1f8f7&pageSize=100&page=1&from=2017-01-01&to=2017-09-13&sources=politico HTTP/1.1" 200 51305
DEBUG:__main__:Total pages (100 per page) for politico results from 2017-01-01 to 2017-09-13 is 1
DEBUG:__main__:

 PROCESSING PAGE: politico?page=1



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newsapi.org
DEBUG:urllib3.connectionpool:https://newsapi.org:443 "GET /v2/everything?apiKey=fd1386b678fd4524b2aa84e3bee1f8f7&pageSize=100&page=1&from=2017-01-01&to=2017-09-13&sources=politico HTTP/1.1" 200 51305
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/13/martin-shkreli-bail-revoked-clinton-242693
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /story/2017/09/13/martin-shkreli-bail-re

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/13/gay-rights-nasa-nominee-bridenstine-242680 HTTP/1.1" 200 17936
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/13/trump-china-national-security-242676
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /story/2017/09/13/trump-china-national-security-242676 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/13/trump-china-national-security-242676 HTTP/1.1" 200 14914
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/13/ted-cruz-porn-tweet-242675
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DE

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/13/war-powers-aumf-rand-paul-senate-242662 HTTP/1.1" 200 16151
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/13/pete-domenici-dies-obituary-242660
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /story/2017/09/13/pete-domenici-dies-obituary-242660 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/13/pete-domenici-dies-obituary-242660 HTTP/1.1" 200 15108
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/agenda/story/2017/09/13/two-democrats-challenge-the-payday-loan-industry-000521
DEBUG:urllib3.connectionpool:Starting new HTTP connecti

DEBUG:__main__:Processing url: http://www.politico.com/tipsheets/morning-tax/2017/09/13/whats-it-add-up-to-222253
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /tipsheets/morning-tax/2017/09/13/whats-it-add-up-to-222253 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /tipsheets/morning-tax/2017/09/13/whats-it-add-up-to-222253 HTTP/1.1" 200 19618
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/tipsheets/morning-cybersecurity/2017/09/13/will-equifax-breach-lead-to-real-change-222257
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /tipsheets/morning-cybersecurity/2017/09/13/will-equifax-breach-lead-to-real-change-222257 HTTP/1.1" 301 0
DEBUG:urllib3.connectionp

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /tipsheets/new-york-playbook/2017/09/13/de-blasio-wins-democratic-nod-monserrate-bows-out-incumbents-stayed-incumbent-222250 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /tipsheets/new-york-playbook/2017/09/13/de-blasio-wins-democratic-nod-monserrate-bows-out-incumbents-stayed-incumbent-222250 HTTP/1.1" 200 25596
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/tipsheets/new-jersey-playbook/2017/09/13/melgens-girlfriend-trashes-prosecutors-fulop-ad-pokes-fun-at-christies-beach-day-more-nj-residents-have-health-insurance-222244
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /tipsheets/new-jersey-playbook/2017/0

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/agenda/story/2017/09/13/five-must-reads-planetary-health-000518
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /agenda/story/2017/09/13/five-must-reads-planetary-health-000518 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /agenda/story/2017/09/13/five-must-reads-planetary-health-000518 HTTP/1.1" 200 12267
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/agenda/story/2017/09/13/food-nutrients-carbon-dioxide-000511
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /agenda/story/2017/09/13/food-nutrients-carbon-dioxide-000511 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new

DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /states/new-york/city-hall/story/2017/09/12/de-blasio-coasts-to-democratic-nomination-for-mayor-114451 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /states/new-york/city-hall/story/2017/09/12/de-blasio-coasts-to-democratic-nomination-for-mayor-114451 HTTP/1.1" 200 14793
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/12/rand-paul-war-powers-242639
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /story/2017/09/12/rand-paul-war-powers-242639 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/12/rand-paul-war-powers-242639 HTTP/1.1" 200 14583
DEBUG:__main_

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /gallery/2017/09/12/usda-beltsville-agricultural-research-center-photos-002483 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /gallery/2017/09/12/usda-beltsville-agricultural-research-center-photos-002483 HTTP/1.1" 200 10649
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: http://www.politico.com/story/2017/09/12/equifax-security-breach-hackers-242623
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): www.politico.com
DEBUG:urllib3.connectionpool:http://www.politico.com:80 "GET /story/2017/09/12/equifax-security-breach-hackers-242623 HTTP/1.1" 301 0
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.politico.com
DEBUG:urllib3.connectionpool:https://www.politico.com:443 "GET /story/2017/09/12/equifax

In [12]:
r.json()['totalResults']

121

# Washington Times

In [14]:
# setup
# use your newsapi key
# update collection, date and source
collection = 'WashTimes'

In [76]:
page = 1
earliest_date = '2017-01-01'
latest_date = '2017-12-31'
source = 'the-washington-times'
pageSize = 100
apiKey = 'fd1386b678fd4524b2aa84e3bee1f8f7'

params = {
    'apiKey'   : apiKey,
    'pageSize' : pageSize,
    'page'     : page,
    'from'     : earliest_date,
    'to'       : latest_date,
    'sources'  : source
}

# base url
api_url = 'https://newsapi.org/v2/everything?'

# get first request to obtain total news count
r = requests.get(api_url, params=params)
totalPages = r.json()['totalResults']//100

log.debug(f'TOTAL PAGES FOR {source}: {totalPages}')

# scrape news
for p in range(page,totalPages):
    log.debug(f'\n\n PROCESSING PAGE: {source+"?page="+str(page)}\n\n\
              ====================================\n\n')
    
    params = {
        'apiKey'   : apiKey,
        'pageSize' : pageSize,
        'page'     : page,
        'from'     : earliest_date,
        'to'       : latest_date,
        'sources'  : source
    }
    
    r = requests.get(api_url, params=params)

    page += 1
    
    for a in r.json()['articles']:
        try:
            log.debug(f"Processing url: {a['url']}")
            if db[collection].find({'url':a['url']}):
                log.debug(f'URL exists in DB. Skipping.')
            else:
                article_date = scrape(a['url'], db, collection)
        except Exception:
            article_date = earliest_date + 1

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newsapi.org
DEBUG:urllib3.connectionpool:https://newsapi.org:443 "GET /v2/everything?apiKey=fd1386b678fd4524b2aa84e3bee1f8f7&pageSize=100&page=1&from=2017-01-01&to=2017-12-31&sources=the-washington-times HTTP/1.1" 200 73971
DEBUG:__main__:TOTAL PAGES FOR the-washington-times: 2
DEBUG:__main__:

 PROCESSING PAGE: the-washington-times?page=1



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): newsapi.org
DEBUG:urllib3.connectionpool:https://newsapi.org:443 "GET /v2/everything?apiKey=fd1386b678fd4524b2aa84e3bee1f8f7&pageSize=100&page=1&from=2017-01-01&to=2017-12-31&sources=the-washington-times HTTP/1.1" 200 73971
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/28/global-warming-films-flop-box-office-2017/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/27/woman-accused-racism-dem-rep-human-rights-activist/
DEBUG

DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/15/illegal-immigration-border-back-obama-levels/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/13/john-wall-returns-wizards-lineup-scores-13-points/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/13/fox-news-host-jeanine-pirro-sued-for-defamation/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/13/giancarlo-stanton-deal-revives-evil-empire/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/13/chuck-grassley-says-republicans-need-decide-if-the/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/dec/13/canseco-tweets-could

DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/28/virginia-mother-charged-after-recording-device/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/28/jarrett-voters-flipped-trump-painful-think-about/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/27/cowboys-dak-prescott-havent-been-same-ezekiel-elli/?
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/27/who-plague-outbreak-madagascar-slowing/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/27/ex-white-house-ethics-lawyer-return-private-firm/
DEBUG:__main__:URL exists in DB. Skipping.
DEBUG:__main__:Processing url: https://www.washingtontimes.com/news/2017/nov/26/trump-slams-democrats

In [77]:
r.json()

{'status': 'ok',
 'totalResults': 240,
 'articles': [{'source': {'id': 'the-washington-times',
    'name': 'The Washington Times'},
   'author': 'The Washington Times http://www.washingtontimes.com',
   'title': "'Global warming' films FLOP...",
   'description': 'Looking for Mueller’s red meat main course Number of cops killed near 50-year low in Trump’s first year Caught in the bubble: Generation I, technology, politics in 2017 Locate anyone instantly, Americans addicted to new search tool. Question of the Day One Da…',
   'url': 'https://www.washingtontimes.com/news/2017/dec/28/global-warming-films-flop-box-office-2017/',
   'urlToImage': 'https://twt-media.washtimes.com/media/image/2017/07/27/7_272017_film-review--an-inconveni-28201.jpg',
   'publishedAt': '2017-12-31T18:01:26Z'},
  {'source': {'id': 'the-washington-times', 'name': 'The Washington Times'},
   'author': 'Mike Rivero',
   'title': 'Woman accused of racism by Rep. Sheila Jackson Lee is human-rights activist',
   'desc

# Slate

In [ ]:
collection = 'slate'
source = 'https://slate.com/news-and-politics/'
page   = 1

utc=pytz.UTC
earliest_date = utc.localize(date_parser('2017-01-01'))

while True:
    log.debug(f'\n\n PROCESSING PAGE: {source+str(page)}\n\n\
              ====================================\n\n')
    s = Source(source+str(page))
    page += 1
    s.download()
    soup = bs.BeautifulSoup(s.html,'lxml')

    # line below needs to be updated per news source
    # to include the specific tags for article text 
    # defined differently for each site
    for link in soup.find('div', {"class":"topic-stories-list"}).findChildren("a" , recursive=False):
        url = link['href']
        log.debug(f'Processing url: {url}')
        
        try:
            article_date = scrape(url, db, collection)
        except Exception:
            article_date = earliest_date + 1 #to make sure scraping continues
        
        # the Atlantic blocks right away after few quick downloads
        # so it requires sleeping, testing showed 1 to 5 seconds is enough
#         sleep(random.uniform(1,5))

    try:
        if article_date < earliest_date:
            log.debug(f'Reached earliest date requested: {article_date}')
            break
    except Exception as e:
        log.debug(f'Exception: {e}')
        continue

DEBUG:__main__:

 PROCESSING PAGE: https://slate.com/news-and-politics/1



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/1 HTTP/1.1" 200 93880
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/californias-deadly-carr-fire-doubles-in-size-as-death-toll-continues-to-rise.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/californias-deadly-carr-fire-doubles-in-size-as-death-toll-continues-to-rise.html HTTP/1.1" 200 95907
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/man-accuses-sean-spicer-of-using-racial-slur-trying-to-fight-him-in-school.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/0

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/the-hot-seats-an-ohio-special-election-comes-down-to-pelosi.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/the-hot-seats-an-ohio-special-election-comes-down-to-pelosi.html HTTP/1.1" 200 100087
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/president-trump-reportedly-signed-off-on-trump-tower-meeting-with-russians-peddling-clinton-dirt.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/president-trump-reportedly-signed-off-on-trump-tower-meeting-with-russians-peddling-clinton-dirt.html HTTP/1.1" 200 96179
DEBUG:__main__:Saved to DB
DEBUG:__main__:

 PROCESSING PAGE: https://slate.com/news-and-politics/2



DEBU

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/what-should-we-expect-from-the-flamboyant-demagogue-cricket-star-whos-poised-to-lead-pakistan.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/what-should-we-expect-from-the-flamboyant-demagogue-cricket-star-whos-poised-to-lead-pakistan.html HTTP/1.1" 200 100997
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/brock-turner-says-he-didnt-attempt-rape-only-outercourse.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/brock-turner-says-he-didnt-attempt-rape-only-outercourse.html HTTP/1.1" 200 97191
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/centrist-democrat

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/trump-white-house-reportedly-suspends-practice-of-releasing-summaries-of-presidents-calls-with-foreign-leaders.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/trump-white-house-reportedly-suspends-practice-of-releasing-summaries-of-presidents-calls-with-foreign-leaders.html HTTP/1.1" 200 95852
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/saul-austerlitz-altamont-book-pot-addiction-is-real-and-trumps-iran-tweet-in-slates-daily-newsletter.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/saul-austerlitz-altamont-book-pot-addiction-is-real-and-trumps-iran-tweet-in-slates-daily-newsletter.html HTTP/1.1" 200 9485

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/u-s-swimmer-ryan-lochte-suspended-by-anti-doping-agency-after-getting-busted-in-the-most-ryan-lochte-possible-way.html HTTP/1.1" 200 95817
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/republican-congressmen-try-a-tv-intervention-with-trump-on-russia.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/republican-congressmen-try-a-tv-intervention-with-trump-on-russia.html HTTP/1.1" 200 98792
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/brett-kavanaughs-criticism-of-united-states-v-nixon-should-worry-robert-mueller.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connecti

...

DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/democrats-can-capitalize-on-donald-trumps-failed-policies-in-the-midwest.html HTTP/1.1" 200 104114
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/correcting-trumps-record-on-russia-how-wisconsin-lost-its-progressives-and-mariia-butinas-methods-in-slates-daily-newsletter.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/correcting-trumps-record-on-russia-how-wisconsin-lost-its-progressives-and-mariia-butinas-methods-in-slates-daily-newsletter.html HTTP/1.1" 200 95689
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/trump-putin-talked-russian-questioning-of-american-sanctions.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/obama-delivers-nelson-mandela-speech-in-south-africa.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/obama-delivers-nelson-mandela-speech-in-south-africa.html HTTP/1.1" 200 97357
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/the-real-threat-to-american-democracy-is-the-right.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/the-real-threat-to-american-democracy-is-the-right.html HTTP/1.1" 200 98795
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/north-carolina-republicans-plan-to-steal-a-state-supreme-court-seat-from-anita-earls-is-backfiring.html
DEBUG:ur

DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/donald-trump-is-fulfilling-all-of-those-obama-conspiracy-theories.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/donald-trump-is-fulfilling-all-of-those-obama-conspiracy-theories.html HTTP/1.1" 200 99011
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/peter-strzok-is-the-hero-we-need.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/peter-strzok-is-the-hero-we-need.html HTTP/1.1" 200 100019
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/republican-legislators-are-troubled-dismayed-perplexed-by-trump-putin-press-conference.html
DEBUG:urllib3.connectionpool:

DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/trump-denounces-u-s-intelligence-on-russia-hacking-praises-putin-denial-as-strong-and-powerful.html HTTP/1.1" 200 97340
DEBUG:__main__:Saved to DB
DEBUG:__main__:

 PROCESSING PAGE: https://slate.com/news-and-politics/10



DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/10 HTTP/1.1" 200 94440
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/john-bolton-had-5-million-reasons-to-work-with-cambridge-analytica.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/john-bolton-had-5-million-reasons-to-work-with-cambridge-analytica.html HTTP/1.1" 200 101944
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/harith-augustus-shooti

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/brett-kavanaughs-record-on-the-rule-of-law-is-much-worse-than-his-defenders-contend.html HTTP/1.1" 200 102967
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/muellers-indictment-of-russian-hackers-is-full-of-clues-about-trumpworld.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com:443 "GET /news-and-politics/2018/07/muellers-indictment-of-russian-hackers-is-full-of-clues-about-trumpworld.html HTTP/1.1" 200 101427
DEBUG:__main__:Saved to DB
DEBUG:__main__:Processing url: https://slate.com/news-and-politics/2018/07/six-big-takeaways-from-muellers-indictment-of-russian-intel-officers.html
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): slate.com
DEBUG:urllib3.connectionpool:https://slate.com: